<a href="https://www.kaggle.com/code/nurielreuven/starbucks-locations-analysis-and-prediction?scriptVersionId=96941413" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

# Starbucks Locations - Analysis and Prediction

By Nuriel Reuven.

Version 1.1 , uploaded on 10.5.22 | Last Updated on 29.5.22
© 2022- All Rights Reserved.

-----------------------------------

Version 1.1 Update:

-Minor spelling corrections.

-Data leaks removed.

-----------------------------------

![](https://nypost.com/wp-content/uploads/sites/2/2020/05/200506-starbucks-reopening-stores.jpg?quality=75&strip=all&w=1116)

-----------------------------------

# Intro

Starbucks is the worlds most popular coffee chain, with 33,833 stores in 80 countries (as for November 2021). Starbucks rapid growth, made it one of the most well known brands, generating almost 30B$ a year. 

In this notebook, we will use a dataset of all of Starbucks locations. We will analyse its distribution in the US and the rest of the world and suggest a model to predict where should new stores be opened, based on a dataset of coffee consumption around the world.

To read more about the datasets:

-**Starbucks locations worldwide**: https://www.kaggle.com/datasets/starbucks/store-locations

-**Coffee consumption by country**: https://www.kaggle.com/datasets/nurielreuven/coffee-consumption-by-country-2022

# Data Exploration

In [1]:
import numpy as np 
import pandas as pd 
from plotly.offline import plot, iplot, init_notebook_mode
import plotly_express as px
init_notebook_mode(connected=True)
import ipywidgets as widgets

In [2]:
data = pd.read_csv('../input/store-locations/directory.csv', sep = ',') 
data.head(8)

Brand  Store Number                Store Name Ownership Type  \
0  Starbucks  47370-257954             Meritxell, 96       Licensed   
1  Starbucks  22331-212325          Ajman Drive Thru       Licensed   
2  Starbucks  47089-256771                 Dana Mall       Licensed   
3  Starbucks  22126-218024                Twofour 54       Licensed   
4  Starbucks  17127-178586              Al Ain Tower       Licensed   
5  Starbucks  17688-182164  Dalma Mall, Ground Floor       Licensed   
6  Starbucks  18182-182165       Dalma Mall, Level 1       Licensed   
7  Starbucks  23359-229184        Debenhams Yas Mall       Licensed   

                    Street Address              City State/Province Country  \
0                Av. Meritxell, 96  Andorra la Vella              7      AD   
1             1 Street 69, Al Jarf             Ajman             AJ      AE   
2     Sheikh Khalifa Bin Zayed St.             Ajman             AJ      AE   
3                  Al Salam Street         Abu Dhabi             AZ      AE   
4  Khaldiya Area, Abu Dhabi Island         Abu Dhabi             AZ      AE   
5             Dalma Mall, Mussafah         Abu Dhabi             AZ      AE   
6             Dalma Mall, Mussafah         Abu Dhabi             AZ      AE   
7                       Yas Island         Abu Dhabi             AZ      AE   

  Postcode Phone Number                 Timezone  Longitude  Latitude  
0    AD500    376818720  GMT+1:00 Europe/Andorra       1.53     42.51  
1      NaN          NaN     GMT+04:00 Asia/Dubai      55.47     25.42  
2      NaN          NaN     GMT+04:00 Asia/Dubai      55.47     25.39  
3      NaN          NaN     GMT+04:00 Asia/Dubai      54.38     24.48  
4      NaN          NaN     GMT+04:00 Asia/Dubai      54.54     24.51  
5      NaN          NaN     GMT+04:00 Asia/Dubai      54.49     24.40  
6      NaN          NaN     GMT+04:00 Asia/Dubai      54.49     24.40  
7      NaN          NaN     GMT+04:00 Asia/Dubai      54.61     24.46

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25600 entries, 0 to 25599
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Brand           25600 non-null  object 
 1   Store Number    25600 non-null  object 
 2   Store Name      25600 non-null  object 
 3   Ownership Type  25600 non-null  object 
 4   Street Address  25598 non-null  object 
 5   City            25585 non-null  object 
 6   State/Province  25600 non-null  object 
 7   Country         25600 non-null  object 
 8   Postcode        24078 non-null  object 
 9   Phone Number    18739 non-null  object 
 10  Timezone        25600 non-null  object 
 11  Longitude       25599 non-null  float64
 12  Latitude        25599 non-null  float64
dtypes: float64(2), object(11)
memory usage: 2.5+ MB


Very few null data we can see. We will look further:

In [4]:
data.isna().sum()

Brand                0
Store Number         0
Store Name           0
Ownership Type       0
Street Address       2
City                15
State/Province       0
Country              0
Postcode          1522
Phone Number      6861
Timezone             0
Longitude            1
Latitude             1
dtype: int64

Like said, except for the postcode and phone number (which we wont need in this notebook), we have very few missing data.

Next we'll see what brands are listed in the dataset:

In [5]:
data['Brand'].value_counts().sort_values(ascending=False)

Starbucks                25249
Teavana                    348
Evolution Fresh              2
Coffee House Holdings        1
Name: Brand, dtype: int64

Well apparently not all stores are of starbucks, after a short google, [Teavana](https://en.wikipedia.org/wiki/Teavana) was a chain that was acquired by Starbucks and was closed down , [Evolution Fresh](https://en.wikipedia.org/wiki/Evolution_Fresh) also became a supplier of products to Starbucks stores and [Coffee House Holdings](https://www.sec.gov/Archives/edgar/data/829224/000119312511317175/d232803dex21.htm/) is a holding subsidary of Starbucks. We can remove all as they are not physical stores.

In [6]:
data = data.query('Brand == "Starbucks"')
data['Brand'].value_counts()

Starbucks    25249
Name: Brand, dtype: int64

And like said before, we would also remove unnecessary columns like phone number and postal:

In [7]:
data.drop(axis=1 , columns=['Store Number','Postcode','Phone Number','Timezone'] , inplace=True)
data.sample(3)

Brand         Store Name Ownership Type             Street Address  \
3683  Starbucks          湖州凤凰时代广场店  Joint Venture              吴兴区, 湖州凤凰时代广场   
7066  Starbucks          Ningyocho  Joint Venture  3-6-7 Nihonbashiningyocho   
9425  Starbucks  Guanajuato Centro       Licensed     Jardin de la Union S/N   

            City State/Province Country  Longitude  Latitude  
3683         湖州市             33      CN     120.09     30.87  
7066     Chuo-ku             13      JP     139.78     35.69  
9425  Guanajuato            GUA      MX    -101.25     21.02

Now we'd like to get an idea of the geographical distribution of the stores, per country,city, and state:

In [8]:
data['Country'].value_counts().sort_values(ascending=False)

US    13311
CN     2734
CA     1415
JP     1237
KR      993
      ...  
CW        3
AW        3
MC        2
LU        2
AD        1
Name: Country, Length: 73, dtype: int64

In [9]:
data['City'].value_counts().sort_values(ascending=False)

上海市              542
Seoul            243
北京市              234
New York         230
London           215
                ... 
Cornelias          1
Twinsburg          1
Wayzata            1
West St. Paul      1
Midrand            1
Name: City, Length: 5401, dtype: int64

In [10]:
data['State/Province'].value_counts().sort_values(ascending=False)

CA     2782
TX     1024
ENG     787
WA      747
11      706
       ... 
DJ        1
65        1
70        1
74        1
SA        1
Name: State/Province, Length: 338, dtype: int64

Also for US states only:

In [11]:
data.query('Country == "US"')['State/Province'].value_counts().sort_values(ascending=False)

CA    2782
TX    1024
WA     747
FL     671
NY     627
IL     562
AZ     479
CO     477
VA     421
OH     366
OR     356
PA     348
NC     330
GA     318
MI     272
MA     262
MD     252
NJ     249
NV     249
IN     215
MO     181
TN     175
MN     175
WI     140
SC     129
CT     118
KY     114
HI      98
UT      97
KS      93
DC      91
IA      87
AL      84
LA      82
OK      77
NM      75
ID      66
NE      56
AR      54
AK      48
MT      36
MS      32
ME      29
RI      26
NH      26
SD      24
DE      24
WV      24
WY      23
ND      13
VT       7
Name: State/Province, dtype: int64

In [12]:
data.query('Country == "US"')['State/Province'].value_counts(normalize=True).apply(lambda x: x*100).sort_values(ascending=False)

CA    20.900008
TX     7.692886
WA     5.611900
FL     5.040944
NY     4.710390
IL     4.222072
AZ     3.598528
CO     3.583502
VA     3.162798
OH     2.749606
OR     2.674480
PA     2.614379
NC     2.479153
GA     2.389002
MI     2.043423
MA     1.968297
MD     1.893171
NJ     1.870633
NV     1.870633
IN     1.615205
MO     1.359778
TN     1.314702
MN     1.314702
WI     1.051762
SC     0.969123
CT     0.886485
KY     0.856435
HI     0.736233
UT     0.728721
KS     0.698670
DC     0.683645
IA     0.653595
AL     0.631057
LA     0.616032
OK     0.578469
NM     0.563444
ID     0.495831
NE     0.420705
AR     0.405680
AK     0.360604
MT     0.270453
MS     0.240403
ME     0.217865
RI     0.195327
NH     0.195327
SD     0.180302
DE     0.180302
WV     0.180302
WY     0.172789
ND     0.097664
VT     0.052588
Name: State/Province, dtype: float64

We would like to work with country names and not codes, and second we can see some city names are not in English. Additionally we would like to add the continent. To solve these issues we will use a library called pycountry:

In [13]:
import pycountry as pc
!pip3 install pycountry_convert
import pycountry_convert as pcc  

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 208.7/208.7 KB 4.4 MB/s eta 0:00:00


In [14]:
data['Country_ISO'] = data['Country']
data['Country'] = data['Country'].apply(lambda country: pc.countries.get(alpha_2=country).name)
data['Continent'] = data['Country_ISO'].apply(lambda country: pcc.country_alpha2_to_continent_code(country)).apply(lambda cont: pcc.convert_continent_code_to_continent_name(cont))
data.sample(5)

Brand                     Store Name Ownership Type  \
272    Starbucks                   Mount Druitt       Licensed   
22953  Starbucks    Target Knoxville West T-151       Licensed   
17801  Starbucks              Downtown LaGrange  Company Owned   
20007  Starbucks  Target Greensboro West T-2108       Licensed   
23338  Starbucks                    I-10 & Mesa  Company Owned   

                                          Street Address            City  \
272                                      Carlisle Avenue       Mt Druitt   
22953                                8040 Ray Mears Blvd  Knoxville West   
17801                                  38 S La Grange Rd       La Grange   
20007  1628 Highwoods Blvd, Elmsley Square Shopping C...      Greensboro   
23338                                   7829 Mesa Street         El Paso   

      State/Province        Country  Longitude  Latitude Country_ISO  \
272              NSW      Australia     150.82    -33.77          AU   
22953             TN  United States     -84.05     35.92          US   
17801             IL  United States     -87.87     41.81          US   
20007             NC  United States     -79.88     36.11          US   
23338             TX  United States    -106.57     31.84          US   

           Continent  
272          Oceania  
22953  North America  
17801  North America  
20007  North America  
23338  North America

And now lets see the distributions again for the new names:

In [15]:
data['Country'].value_counts().sort_values(ascending=False)

United States         13311
China                  2734
Canada                 1415
Japan                  1237
Korea, Republic of      993
                      ...  
Curaçao                   3
Aruba                     3
Monaco                    2
Luxembourg                2
Andorra                   1
Name: Country, Length: 73, dtype: int64

In [16]:
data['Country'].value_counts(normalize=True)

United States         0.527189
China                 0.108282
Canada                0.056042
Japan                 0.048992
Korea, Republic of    0.039328
                        ...   
Curaçao               0.000119
Aruba                 0.000119
Monaco                0.000079
Luxembourg            0.000079
Andorra               0.000040
Name: Country, Length: 73, dtype: float64

In [17]:
data['Continent'].value_counts().sort_values(ascending=False)

North America    15381
Asia              7496
Europe            1873
South America      410
Oceania             46
Africa              43
Name: Continent, dtype: int64

In [18]:
data['Continent'].value_counts(normalize=True)

North America    0.609173
Asia             0.296883
Europe           0.074181
South America    0.016238
Oceania          0.001822
Africa           0.001703
Name: Continent, dtype: float64

-----------------------------------

# Graphs & Maps

Here we would visualize the data we have explored before, we will visualize both in maps (as most of our data is geographical) and graphs (scatter, histogram, boxplot etc..)

In [19]:
import ipywidgets as widgets

In [20]:
map1 = px.scatter_geo(data, lat='Latitude', lon='Longitude' , hover_name='Store Name' , size_max = 10 , title='Starbucks locations worldwide')
map1.show()

In [21]:
map2data = data.query('Country_ISO == "US"')
map2 = px.scatter_geo(map2data , locationmode = 'USA-states' ,scope='usa' , lat='Latitude', lon='Longitude' , hover_name='Store Name' , size_max = 10 , title='Starbucks locations United States')
map2.show()

In [22]:
map3data = data['Country'].value_counts().rename('Counts')
map3 = px.scatter_geo(map3data, locationmode = 'country names' , locations=map3data.index ,color='Counts' , hover_data=['Counts'] , color_continuous_scale='RdBU' , title = 'No. of stores per country')
map3.show()

**Note:** this map can be drawn with size of each dot indicating the no. of stores , but due to large difference of the numbers the dots appear almost invisible, below is the code to draw this graph:

In [23]:
#map3 = px.scatter_geo(map3data, locationmode = 'country names' , locations=map3data.index ,color='Counts' , size='Counts' , hover_data=['Counts'] , color_continuous_scale='RdBU' , title = 'No. of stores per country')
#map3.show()

In [24]:
map4data = data.query('Country_ISO == "US"')['State/Province'].value_counts().rename('Counts')

map4 = px.scatter_geo(map4data, locationmode = 'USA-states' , locations=map4data.index , size='Counts' ,color='Counts' , hover_data=['Counts'] , color_continuous_scale='RdBu' , scope='usa'  , title = 'No. of stores per state in United States')
map4.show()


For the histograms, we would mostly use log scale for the y axis since as said, the stores counts are on different magnitues, of 100 times and 1000 times more.

Lets see the ownership type distribution per country:

In [25]:
px.histogram(data , x='Country' , color='Ownership Type' , labels={'count' : 'No. of Stores'} , title='Ownership type per country' , color_discrete_sequence=px.colors.qualitative.Pastel , log_y=True).update_xaxes(categoryorder = 'total descending')

**Note:** Below is cities and countries stores distribution, the cities distribution is very computational heavy so we will not draw it:

In [26]:
# px.histogram(data.dropna() , x='Country' , color='City' , title='No. of stores per country & city' , color_discrete_sequence=px.colors.qualitative.Pastel , log_y=True).update_xaxes(categoryorder = 'total descending')

In [27]:
def graph_city_by_country(data,option):
    graphdata = data.query(f'Country == "{option}"')
    return px.histogram(graphdata , x='City' , title='Cities stores count per country').update_xaxes(categoryorder = 'total descending')

@widgets.interact
def city_by_country(option=widgets.Dropdown(options = data['Country'].unique(), description='Country:',disabled=False)):
    return graph_city_by_country(data,option)

interactive(children=(Dropdown(description='Country:', options=('Andorra', 'United Arab Emirates', 'Argentina'…

Continents and countries stores distribution:

In [28]:
px.histogram(data , x='Continent' , color='Country', labels={'count' : 'No. of Stores'} , title='No. of stores per continent & country' , color_discrete_sequence=px.colors.qualitative.Pastel , log_y=True).update_xaxes(categoryorder = 'total descending')

In [29]:
def graph_country_by_continent(data,option):
    graphdata = data.query(f'Continent == "{option}"')
    return px.histogram(graphdata , x='Country' , labels={'count' : 'No. of Stores'} , title='No. of stores per continent & country').update_xaxes(categoryorder = 'total descending')

@widgets.interact
def country_by_continent(option=widgets.Dropdown(options = data['Continent'].unique(), description='Continent:',disabled=False)):
    return graph_country_by_continent(data,option)

interactive(children=(Dropdown(description='Continent:', options=('Europe', 'Asia', 'South America', 'Oceania'…

And a US stores distribution per state:

In [30]:
px.histogram(data.query("Country_ISO == 'US'") , x='State/Province' , color='City' , labels={'count' : 'No. of Stores'} , title='No. of stores per city & US state' , color_discrete_sequence=px.colors.qualitative.Pastel , log_y=True).update_xaxes(categoryorder = 'total descending')

In [31]:
def graph_city_by_state(data,option):
    graphdata = data.query("Country_ISO == 'US'").rename(columns = {'State/Province' : 'State'}).query(f'State == "{option}"')
    return px.histogram(graphdata , x='City', labels={'count' : 'No. of Stores'} , title='No. of stores per city & US state').update_xaxes(categoryorder = 'total descending')

@widgets.interact
def city_by_state(option=widgets.Dropdown(options = data.query("Country_ISO == 'US'")['State/Province'].unique(), description='State:',disabled=False)):
    return graph_city_by_state(data,option)

interactive(children=(Dropdown(description='State:', options=('AK', 'AL', 'AR', 'AZ', 'CA', 'CO', 'CT', 'DC', …

After visualizing our data, we can now continue to modeling it.

-----------------------------------

# Modeling

As said, we are trying to model countries stores distribution versus the country's coffee consumption. For that we would load the dataset with the world coffee consumption and merge it to our dataset:

In [32]:
consdata = pd.read_csv('../input/coffee-consumption-by-country-2022/CoffeeConsumption.csv', sep = ',') 
consdata.sample(3)

country  totCons2019  perCapitaCons2016
21  Tunisia        508.0                NaN
5    Russia       4820.0                NaN
12  Belgium       1185.0               15.0

In [33]:
consdata.rename(columns={"country": "Country" , "totCons2019": "Total", "perCapitaCons2016": "PerCapita"} , inplace=True)
consdata.head(3)

Country    Total  PerCapita
0  United States  27310.0       9.26
1        Germany   8670.0      12.13
2          Japan   7551.0        NaN

In [34]:
x = pd.DataFrame(data['Country'].value_counts().rename('Stores_count'))
x.reset_index(inplace=True)
x.rename(columns = {'index' : 'Country'} , inplace=True)
consdata = consdata.merge(x , on='Country')
consdata

Country    Total  PerCapita  Stores_count
0    United States  27310.0       9.26         13311
1          Germany   8670.0      12.13           160
2            Japan   7551.0        NaN          1237
3           France   6192.0      11.90           132
4   United Kingdom   3770.0        NaN           901
5            Spain   3253.0       9.92           101
6           Poland   2501.0        NaN            53
7      Netherlands   2030.0      18.52            59
8           Sweden   1769.0      18.00            18
9          Finland   1348.0      26.45             8
10         Belgium   1185.0      15.00            19
11         Austria   1173.0      13.45            18
12          Greece   1139.0      11.90            28
13         Romania   1108.0        NaN            27
14     Switzerland   1073.0      17.42            61
15        Portugal    931.0       9.48            11
16         Denmark    778.0      19.18            21
17          Norway    771.0      21.82            17
18        Bulgaria    423.0        NaN             5
19         Hungary    418.0        NaN            16
20         Ireland    370.0        NaN            73
21        Slovakia    227.0        NaN             3
22      Luxembourg    224.0      14.33             2
23          Cyprus    115.0      10.80            10
24         Lebanon      NaN      10.58            29
25          Canada      NaN      14.33          1415
26          Brazil      NaN      12.79           102

We will try to plot the stores count vs total and per capita consumption to look for a regression fit to describe our data. We can see the stores count and total consumption are of different magnitues so the intuition (already from the histogram in previous chapter) will be to plot with log axis:

In [35]:
px.scatter(consdata , x='PerCapita' , y='Stores_count' , labels={'Stores_count' : 'No. of Stores (log)' , 'PerCapita' : 'Per capita coffee consumption'} , title='No. of stores vs. Per capita coffee consumption' , hover_data=['Country'] , log_y = True)

In [36]:
px.scatter(consdata , x='Total' , y='Stores_count' , labels={'Stores_count' : 'No. of Stores (log)' , 'Total' : 'Total coffee consumption (log)'} , title='No. of stores vs. Total coffee consumption' , hover_data=['Country'] , log_x = True , log_y=True)

Visually we can see theres a good chance there is a linear fit in both graphs. So we will try to use *Linear Regression* for our model. We will also choose another model to try and see if we get better results by chance. The extra model we chose is *Decision Tree Regressor*.
Last few imports and edits for our data and were ready to go:

In [37]:
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import LeavePOut
from sklearn.tree import DecisionTreeRegressor
from sklearn import preprocessing

import math as math
import statistics

In [38]:
consdata['Stores_count_log'] = consdata['Stores_count'].astype(float).apply(lambda x: math.log(x))
consdata['Total_log'] = consdata['Total'].astype(float).apply(lambda x: math.log(x))
consdata

Country    Total  PerCapita  Stores_count  Stores_count_log  \
0    United States  27310.0       9.26         13311          9.496346   
1          Germany   8670.0      12.13           160          5.075174   
2            Japan   7551.0        NaN          1237          7.120444   
3           France   6192.0      11.90           132          4.882802   
4   United Kingdom   3770.0        NaN           901          6.803505   
5            Spain   3253.0       9.92           101          4.615121   
6           Poland   2501.0        NaN            53          3.970292   
7      Netherlands   2030.0      18.52            59          4.077537   
8           Sweden   1769.0      18.00            18          2.890372   
9          Finland   1348.0      26.45             8          2.079442   
10         Belgium   1185.0      15.00            19          2.944439   
11         Austria   1173.0      13.45            18          2.890372   
12          Greece   1139.0      11.90            28          3.332205   
13         Romania   1108.0        NaN            27          3.295837   
14     Switzerland   1073.0      17.42            61          4.110874   
15        Portugal    931.0       9.48            11          2.397895   
16         Denmark    778.0      19.18            21          3.044522   
17          Norway    771.0      21.82            17          2.833213   
18        Bulgaria    423.0        NaN             5          1.609438   
19         Hungary    418.0        NaN            16          2.772589   
20         Ireland    370.0        NaN            73          4.290459   
21        Slovakia    227.0        NaN             3          1.098612   
22      Luxembourg    224.0      14.33             2          0.693147   
23          Cyprus    115.0      10.80            10          2.302585   
24         Lebanon      NaN      10.58            29          3.367296   
25          Canada      NaN      14.33          1415          7.254885   
26          Brazil      NaN      12.79           102          4.624973   

    Total_log  
0   10.215008  
1    9.067624  
2    8.929435  
3    8.731013  
4    8.234830  
5    8.087333  
6    7.824446  
7    7.615791  
8    7.478170  
9    7.206377  
10   7.077498  
11   7.067320  
12   7.037906  
13   7.010312  
14   6.978214  
15   6.836259  
16   6.656727  
17   6.647688  
18   6.047372  
19   6.035481  
20   5.913503  
21   5.424950  
22   5.411646  
23   4.744932  
24        NaN  
25        NaN  
26        NaN

Since we can see we have a relatively very small dataset (only 26 rows and even some of them are NaNs), we might have a problem fitting a linear line for very few observations. We will try to improve our Linear Regression model using *Leave P Out Cross Vaildation*. This method was chosen because although computational heavy, for very small dataset like ours its bearable and gives us many scores calculations we can average on.

## Stores vs Per Capita consumption

### Linear Regression

In [39]:
x = consdata['PerCapita'].loc[(consdata['PerCapita'].isna() == False) & (consdata['Stores_count_log'].isna() == False)].reset_index(drop=True)
y = consdata['Stores_count_log'].loc[(consdata['PerCapita'].isna() == False) & (consdata['Stores_count_log'].isna() == False)].reset_index(drop=True)

#### Leave P Out Cross Vaildation

In [40]:
lpoparam = 4
lpo = LeavePOut(lpoparam)

r2list = []
for train_index, test_index in lpo.split(x):
    x_train, x_test = np.array(x[train_index]).reshape(-1,1), np.array(x[test_index]).reshape(-1,1)
    y_train, y_test = np.array(y[train_index]).reshape(-1,1), np.array(y[test_index]).reshape(-1,1)
    reg = LinearRegression()
    reg.fit(x_train,y_train)
    y_pred = reg.predict(x_test)
    r2list.append(r2_score(y_test, y_pred))
    
print(f'Leave P-Out of {lpoparam} with R2 mean of {statistics.mean(r2list)} with maximum R2 of {max(r2list)}')

Leave P-Out of 4 with R2 mean of -1.9981020334485202 with maximum R2 of 0.9925271300171139


#### Normal

In [41]:
x_train, x_test, y_train, y_test = train_test_split( x , y , test_size=0.3 , random_state=42)
reg = LinearRegression()
reg.fit(np.array(x_train).reshape(-1,1),np.array(y_train).reshape(-1,1))
y_pred = reg.predict(np.array(x_test).reshape(-1,1))
r2_score(np.array(y_test).reshape(-1,1), y_pred) 
StoVsCapParams = reg.coef_

### Regression Tree

In [42]:
x_train, x_test, y_train, y_test = train_test_split( x , y , test_size=0.3 , random_state=42)
reg = LinearRegression()
reg.fit(np.array(x_train).reshape(-1,1),np.array(y_train).reshape(-1,1))
y_pred = reg.predict(np.array(x_test).reshape(-1,1))
r2_score(np.array(y_test).reshape(-1,1), y_pred)

0.06263744670720395

We can see our Leave P Out model performed very badly, this is because there are only 4 test samples and in some formats of the train-test split the test samples have very bad linear correlation (it also works the other way ofcourse, as we can see for one run we got an R2 of 0.99 indicating almost perfect linear correlation). changing the P param also didnt change the R2 by much and only cause longer computational time. The Regression Tree performed better, though also didnt improve our R2. 

## Stores vs Total consumption

### Linear Regression

In [43]:
x = consdata['Total_log'].loc[(consdata['Total_log'].isna() == False) & (consdata['Stores_count_log'].isna() == False)].reset_index(drop=True)
y = consdata['Stores_count_log'].loc[(consdata['Total_log'].isna() == False) & (consdata['Stores_count_log'].isna() == False)].reset_index(drop=True)


#### Leave P Out Cross Vaildation

In [44]:
lpoparam = 4
x = consdata['Total_log'].loc[consdata['Total_log'].isna() == False].reset_index(drop=True)
y = consdata['Stores_count_log'].loc[consdata['Total_log'].isna() == False].reset_index(drop=True)
lpo = LeavePOut(lpoparam)

r2list = []
for train_index, test_index in lpo.split(x):
    x_train, x_test = np.array(x[train_index]).reshape(-1,1), np.array(x[test_index]).reshape(-1,1)
    y_train, y_test = np.array(y[train_index]).reshape(-1,1), np.array(y[test_index]).reshape(-1,1)
    reg = LinearRegression()
    reg.fit(x_train,y_train)
    y_pred = reg.predict(x_test)
    r2list.append(r2_score(y_test, y_pred))
    
print(f'Leave P-Out of {lpoparam} with R2 mean of {statistics.mean(r2list)} with maximum R2 of {max(r2list)}')

Leave P-Out of 4 with R2 mean of -0.4951376724398743 with maximum R2 of 0.9638889792222343


#### Normal

In [45]:
x_train, x_test, y_train, y_test = train_test_split( x , y , test_size=0.3 , random_state=42)
reg = LinearRegression()
reg.fit(np.array(x_train).reshape(-1,1),np.array(y_train).reshape(-1,1))
y_pred = reg.predict(np.array(x_test).reshape(-1,1))
r2_score(np.array(y_test).reshape(-1,1), y_pred)
StoVsTotParams = reg.coef_

### Decision Tree Regression

In [46]:
x_train, x_test, y_train, y_test = train_test_split( x , y , test_size=0.3 , random_state=42)
reg = DecisionTreeRegressor(random_state=42)
reg.fit(np.array(x_train).reshape(-1,1),np.array(y_train).reshape(-1,1))
y_pred = reg.predict(np.array(x_test).reshape(-1,1))
r2_score(np.array(y_test).reshape(-1,1), y_pred)

0.6978893763605905

Once again, the Leave P Out method gave us bad results, while the decision tree gave us relatively good results with R2 of 0.69, tho its still low compared to the  linear regression which gave us an R2 of 0.72 , which indicates good prediction.

We will extract the line coefficients from the plotly graph before to calculate what

## Stores prediction

After fitting our linear line, we will try to predict potential locations for future stores opening and expansion. For that we will use the line generated from our plotly diagram of stores vs total consumption of the * **train set** * (We will not use the entire data set trendline to prevent data leaking and sklearn does not provide the fitted line coefficients , so this is our best estimator), since its linear fit is much better. We will divide the stores into 2 categories - **Below the line** , meaning the country is 'underpopulated' with stores, that there are not enough stores to meet the total coffee consumption of that country and there is room for further expansion. Countries **above the line** meaning the country is 'overpopulated' with stores - or that there are too many stores to meet the total coffee consumption of that country. To calculate the underpopulated-overpopulated ratio , we will mark Y as the actual store count , and Y0 is as what the store count should be, according to the fitting line. Therefore its easy to see that the difference Y-Y0 will give us the ratio, which is basically the *residuals*. We would show it in precentage %.

In [47]:
# Line params from the graph
train_reg_line = px.scatter(consdata, x='Total_log', y='Stores_count_log', labels={'Stores_count_log' : 'No. of Stores (log)' , 'Total_log' : 'Total coffee consumption (log)'} , title='No. of stores vs. Total coffee consumption' ,  hover_data=['Country'] , trendline="ols" , trendline_color_override='#FF0000')
a = px.get_trendline_results(train_reg_line).px_fit_results.iloc[0].params[1]
b = px.get_trendline_results(train_reg_line).px_fit_results.iloc[0].params[0]

# Calculation
StoresTotalData = consdata[['Country','Total_log','Stores_count_log']].loc[(consdata['Total_log'].isna() == False)]
StoresTotalData['Value %'] = list(range(0,len(StoresTotalData)))
StoresTotalData['Value %'] = StoresTotalData['Value %'].apply(lambda x: round((StoresTotalData.iloc[x]['Stores_count_log'] - a*StoresTotalData.iloc[x]['Total_log'] - b)*100 / (a*StoresTotalData.iloc[x]['Total_log'] - b),2))
StoresTotalData[['Country','Value %']].sort_values(by='Value %', ascending=False)

Country  Value %
20         Ireland    16.79
23          Cyprus    15.05
4   United Kingdom    10.54
0    United States     9.68
2            Japan     6.59
14     Switzerland     4.59
19         Hungary     4.22
16         Denmark     0.23
17          Norway    -1.16
12          Greece    -1.19
7      Netherlands    -1.19
13         Romania    -1.20
5            Spain    -1.63
21        Slovakia    -2.40
6           Poland    -3.56
10         Belgium    -4.14
11         Austria    -4.41
18        Bulgaria    -4.47
3           France    -4.90
22      Luxembourg    -5.45
15        Portugal    -5.81
1          Germany    -6.19
8           Sweden    -7.73
9          Finland   -10.94

In [48]:
px.bar(StoresTotalData, x='Country' , y='Value %' , hover_data=['Value %'] , labels={'Value %' : '% difference of stores count'} , title = '% Difference of stores count per country', text_auto=True).update_xaxes(categoryorder = 'total descending')

We can see that Ireland, Cyprus and United Kingdom are overpopulated with stores (suprisingly US with the highest abseloute store count is only 4th). The 3 most underpopulated countries are Finland, Sweden and Germany. In general, suprisingly, we can see most countries are below the line, meaning in most countries there is expansion potential!

-----------------------------------

## Summary

In this notebook, we showed an analysis of a dataset of Starbucks stores location and visualized it.

Several models were built to fit the total coffee consumption and per capita consumption to the Starbucks stores count in that country. Of those the Linear Regression showed the best fit with R2 of ~0.72.

Using the linear fit of the total consumption, we calculated the theoretical and actual stores count in that country, to try and see if the country is underpopulated with stores to meet the coffee consumption, and has potential to expand or overpopulated, which means there are more stores than the actual consumption of coffee in that country.

Obviously total coffee consumption alone is not the only consideration of wether the country is under/over populated with stores, but for future work several parameters can be added to the model to try to predict more accurately the exapnsion potential (For example - GDP, Coffee prices, New store opening price, competition, sold items distribution etc..)